# Imports

In [1]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline
#%matplotlib notebook
import sys
###
#!pip install openslide-python
#https://github.com/deroneriksson/python-wsi-preprocessing/
###
sys.path.append('../python-wsi-preprocessing/')
from deephistopath.wsi import slide, filter, tiles, util

import fastai
from fastai.vision import *
from fastai.core import parallel

import pandas as pd
import numpy as np
import os
from pathlib import Path
from functools import partial, update_wrapper
from tqdm import tqdm_notebook as tqdm
from enum import Enum
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from PIL import Image
import cv2
import openslide
from openslide.lowlevel import *
Image.MAX_IMAGE_PIXELS = 10000000000

PATH = Path('/home/Deep_Learner/private/network/datasets/Hypophysenadenome/')
FONT_PATH=PATH/'1984-Happines-Regular.ttf'
WSIS_CORTICOTROP = PATH/'corticotrop'
WSIS_GONADOTROP = PATH/'gonadotrop'
ROIS_CORTICOTROP = PATH/'corticotrop_ROIs'
ROIS_CORTICOTROP_FILTERED = PATH/'rois_corticotrop_filtered'
ROIS_GONADOTROP = PATH/'gonadotrop_ROIs'
ROIS_GONADOTROP_FILTERED = PATH/'rois_gonadotrop_filtered'
TILES_CORTICOTROP = PATH/'tiles_corticotrop'
TILES_GONADOTROP = PATH/'tiles_gonadotrop'
TILES_CORTICOTROP_EXTRA = PATH/'tiles_corticotrop_extra'
TILES_GONADOTROP_EXTRA = PATH/'tiles_gonadotrop_extra'

ROIS_EXPERIMENTING = PATH/'rois_experimenting'
ROIS_EXPERIMENTING_FILTERED = PATH/'rois_experimenting_filtered'
TILES_EXPERIMENTING = PATH/'tiles_experimenting'

PATH_RELAPSE = Path('/home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/')
RELAPSE_WSIS_EXPERIMENTING = PATH_RELAPSE/'wsis_experimenting'
RELAPSE_IMAGES_EXPERIMENTING = PATH_RELAPSE/'imgs_experimenting'
RELAPSE_IMAGES_FILTERED_EXPERIMENTING = PATH_RELAPSE/'imgs_filtered_experimenting'
RELAPSE_TILES_EXPERIMENTING = PATH_RELAPSE/'tiles_experimenting'

NONE_RELAPSE_WSIS = PATH_RELAPSE/'wsis_non_relapse'
NONE_RELAPSE_IMAGES = PATH_RELAPSE/'imgs_non_relapse'
NONE_RELAPSE_IMAGES_FILTERED = PATH_RELAPSE/'imgs_filtered_non_relapse'
NONE_RELAPSE_TILES = PATH_RELAPSE/'tiles_non_relapse'

RELAPSE_WSIS = PATH_RELAPSE/'wsis_relapse'
RELAPSE_IMAGES = PATH_RELAPSE/'imgs_relapse'
RELAPSE_IMAGES_FILTERED = PATH_RELAPSE/'imgs_filtered_relapse'
RELAPSE_TILES = PATH_RELAPSE/'tiles_relapse'


def show(np):
    return util.np_to_pil(np)

Path.ls = lambda x: [p for p in list(x.iterdir()) if '.ipynb_checkpoints' not in p.name]

def show_multiple_images(path, rows = 3, figsize=(128, 64)):
    imgs = [open_image(p) for p in path.ls()]
    show_all(imgs=imgs, r=rows, figsize=figsize)
    
def show_multiple_images_big(path:pathlib.Path):
    for p in path.ls():
        plt.imshow(mpimg.imread(str(p)))
        plt.show()
        
def get_wsi_name_from_path(path):
    split = path.stem.split('-')
    return f'{split[0]}-{split[1]}-{split[2]}-{split[3]}'
        
class AdenomaType(Enum):
    experimenting = 0
    corticotrop = 1
    gonadotrop = 2
    relapse_experimenting = 3
    relapse = 4
    non_relapse = 5
    corticotrop_extra = 6
    gonadotrop_extra = 7

In [2]:
adenomaType = AdenomaType.gonadotrop_extra

if adenomaType == AdenomaType.gonadotrop:
    rois_filtered_path = ROIS_GONADOTROP_FILTERED
    rois_path = ROIS_GONADOTROP
    tiles_path = TILES_GONADOTROP
    
if adenomaType == AdenomaType.corticotrop:
    rois_filtered_path = ROIS_CORTICOTROP_FILTERED
    rois_path = ROIS_CORTICOTROP
    tiles_path = TILES_CORTICOTROP
    
if adenomaType == AdenomaType.gonadotrop_extra:
    wsi_path = WSIS_GONADOTROP
    rois_filtered_path = ROIS_GONADOTROP_FILTERED
    rois_path = ROIS_GONADOTROP
    tiles_path = TILES_GONADOTROP_EXTRA
    
if adenomaType == AdenomaType.corticotrop_extra:
    wsi_path = WSIS_CORTICOTROP
    rois_filtered_path = ROIS_CORTICOTROP_FILTERED
    rois_path = ROIS_CORTICOTROP
    tiles_path = TILES_CORTICOTROP_EXTRA
    
if adenomaType == AdenomaType.experimenting:
    wsi_path = ROIS_EXPERIMENTING
    rois_filtered_path = ROIS_EXPERIMENTING_FILTERED
    rois_path = ROIS_EXPERIMENTING
    tiles_path = TILES_EXPERIMENTING
    
if adenomaType == AdenomaType.relapse_experimenting:
    wsi_path = RELAPSE_WSIS_EXPERIMENTING
    rois_filtered_path = RELAPSE_IMAGES_FILTERED_EXPERIMENTING
    rois_path = RELAPSE_IMAGES_EXPERIMENTING
    tiles_path = RELAPSE_TILES_EXPERIMENTING
    
if adenomaType == AdenomaType.relapse:
    wsi_path = RELAPSE_WSIS
    rois_path = RELAPSE_IMAGES
    rois_filtered_path = RELAPSE_IMAGES_FILTERED
    tiles_path = RELAPSE_TILES  
    
if adenomaType == AdenomaType.non_relapse:
    wsi_path = NONE_RELAPSE_WSIS
    rois_path = NONE_RELAPSE_IMAGES
    rois_filtered_path = NONE_RELAPSE_IMAGES_FILTERED
    tiles_path = NONE_RELAPSE_TILES

In [3]:
rois_path.mkdir(exist_ok=True)
rois_filtered_path.mkdir(exist_ok=True)
tiles_path.mkdir(exist_ok=True)

# Overwrite parts of wsi lib

In [4]:
def score_t(tissue_percent, combined_factor):
    
    #use this, if you only care that there is any tissue in the tile
    #return (tissue_percent ** 2) * np.log(1 + combined_factor) / 1000.0

    #use this, if you want tissue with lots of cells
    return tissue_percent * combined_factor / 1000.0

In [5]:
slide.SCALE_FACTOR = 2


slide.BASE_DIR = PATH/'data'
slide.SRC_TRAIN_EXT = "ndpi"
tiles.SUMMARY_TITLE_FONT_PATH = str(FONT_PATH)
tiles.FONT_PATH = str(FONT_PATH)
tiles.DISPLAY_TILE_SUMMARY_LABELS = True
tiles.LABEL_ALL_TILES_IN_TOP_TILE_SUMMARY = True
tiles.BORDER_ALL_TILES_IN_TOP_TILE_SUMMARY = True
tiles.TISSUE_LOW_THRESH = 20

tiles.ROW_TILE_SIZE = 1024
tiles.COL_TILE_SIZE = 1024

##################################################################################################################

slide.open_slide = slide.open_image

##################################################################################################################

def get_image_path(folder_path, slide_num):
    return folder_path.ls()[slide_num]

slide.get_filter_image_result = partial(get_image_path, rois_filtered_path)
slide.get_training_image_path = partial(get_image_path, rois_path)
slide.get_training_slide_path = partial(get_image_path, wsi_path)

##################################################################################################################

def parse_dimensions_from_image_filename(img_path):
    shape = slide.open_image_np(img_path).shape
    return shape[1], shape[0], shape[1], shape[0]

slide.parse_dimensions_from_image_filename = parse_dimensions_from_image_filename

##################################################################################################################

def tile_to_pil_tile(tile):
  """
  Convert tile information into the corresponding tile as a PIL image read from the whole-slide image file.

  Args:
    tile: Tile object.

  Return:
    Tile as a PIL image.
  """
  t = tile
  filepath = slide.get_training_image_path(t.slide_num)
  img = slide.open_image_np(filepath)
  #x, y = t.o_c_s, t.o_r_s
  #w, h = t.o_c_e - t.o_c_s, t.o_r_e - t.o_r_s
  tile = img[int(t.o_r_s/slide.SCALE_FACTOR):int(t.o_r_e/slide.SCALE_FACTOR), int(t.o_c_s/slide.SCALE_FACTOR):int(t.o_c_e/slide.SCALE_FACTOR),:]
  tile_pil = util.np_to_pil(tile)
  return tile_pil

tiles.tile_to_pil_tile = tile_to_pil_tile

##################################################################################################################
def get_tile_image_path(tile):
  """
  Obtain tile image path based on tile information such as row, column, row pixel position, column pixel position,
  pixel width, and pixel height.

  Args:
    tile: Tile object.

  Returns:
    Path to image tile.
  """
  t = tile
  roi_name = slide.get_training_image_path(t.slide_num).stem
  tile_path = os.path.join(PATH, tiles_path,
                           roi_name + "-" + 'tile' + "-r%d-c%d-x%d-y%d-w%d-h%d" % (
                             t.r, t.c, t.o_c_s, t.o_r_s, t.o_c_e - t.o_c_s, t.o_r_e - t.o_r_s) + "." + 'png')
  return tile_path

slide.get_tile_image_path = get_tile_image_path

##################################################################################################################

def top_tiles(self):
    """
    Retrieve the top-scoring tiles.

    Returns:
       List of the top-scoring tiles.
    """
    sorted_tiles = self.tiles_by_score()
    top_tiles = [tile for tile in sorted_tiles
                 if check_tile(tile)]
    print(f'Number of top tiles/all tiles: {len(top_tiles)}/{len(sorted_tiles)}')
    return top_tiles

def check_tile(tile):
    width = tile.o_c_e - tile.o_c_s
    height = tile.o_r_e - tile.o_r_s
    return tile.score > 0.55 and width >= 0.7*tiles.COL_TILE_SIZE and height >= 0.7*tiles.ROW_TILE_SIZE


tiles.TileSummary.top_tiles = top_tiles

##################################################################################################################
from deephistopath.wsi.tiles import (hsv_saturation_and_value_factor, 
                                     hsv_purple_pink_factor, 
                                     tissue_quantity_factor, 
                                     tissue_quantity)

def score_tile(np_tile, tissue_percent, slide_num, row, col):
  """
  Score tile based on tissue percentage, color factor, saturation/value factor, and tissue quantity factor.

  Args:
    np_tile: Tile as NumPy array.
    tissue_percent: The percentage of the tile judged to be tissue.
    slide_num: Slide number.
    row: Tile row.
    col: Tile column.

  Returns tuple consisting of score, color factor, saturation/value factor, and tissue quantity factor.
  """
  color_factor = hsv_purple_pink_factor(np_tile)
  s_and_v_factor = hsv_saturation_and_value_factor(np_tile)
  amount = tissue_quantity(tissue_percent)
  quantity_factor = tissue_quantity_factor(amount)
  combined_factor = color_factor * s_and_v_factor
  score = score_t(tissue_percent, combined_factor)
  # scale score to between 0 and 1
  score = 1.0 - (10.0 / (10.0 + score))
  #print(f'tp: {tissue_percent}')
  #print(f'cf: {combined_factor}')
  #print(f'score: {score}')  
  return score, color_factor, s_and_v_factor, quantity_factor

tiles.score_tile = score_tile
#tiles.score_tile = tiles.score_tile
#############################################################################################################

def _load_image(buf, size):
        '''buf must be a buffer.'''

        # Load entire buffer at once if possible
        MAX_PIXELS_PER_LOAD = (1 << 29) - 1
        # Otherwise, use chunks smaller than the maximum to reduce memory
        # requirements
        PIXELS_PER_LOAD = 1 << 26

        def do_load(buf, size):
            '''buf can be a string, but should be a ctypes buffer to avoid an
            extra copy in the caller.'''
            # First reorder the bytes in a pixel from native-endian aRGB to
            # big-endian RGBa to work around limitations in RGBa loader
            rawmode = (sys.byteorder == 'little') and 'BGRA' or 'ARGB'
            buf = PIL.Image.frombuffer('RGBA', size, buf, 'raw', rawmode, 0, 1)
            # Image.tobytes() is named tostring() in Pillow 1.x and PIL
            buf = (getattr(buf, 'tobytes', None) or buf.tostring)()
            # Now load the image as RGBA, undoing premultiplication
            return PIL.Image.frombuffer('RGBA', size, buf, 'raw', 'RGBa', 0, 1)

        # Fast path for small buffers
        w, h = size
        if w * h <= MAX_PIXELS_PER_LOAD:
            return do_load(buf, size)

        # Load in chunks to avoid OverflowError in PIL.Image.frombuffer()
        # https://github.com/python-pillow/Pillow/issues/1475
        if w > PIXELS_PER_LOAD:
            # We could support this, but it seems like overkill
            raise ValueError('Width %d is too large (maximum %d)' %
                    (w, PIXELS_PER_LOAD))
        rows_per_load = PIXELS_PER_LOAD // w
        img = PIL.Image.new('RGBA', (w, h))
        for y in range(0, h, rows_per_load):
            rows = min(h - y, rows_per_load)
            if sys.version[0] == '2':
                chunk = buffer(buf, 4 * y * w, 4 * rows * w)
            else:
                # PIL.Image.frombuffer() won't take a memoryview or
                # bytearray, so we can't avoid copying
                chunk = memoryview(buf)[y * w:(y + rows) * w].tobytes()
            img.paste(do_load(chunk, (w, rows)), (0, y))
        return img

openslide.lowlevel._load_image = _load_image


def slide_to_scaled_pil_image(slide_filepath):
  """
  Convert a WSI training slide to a scaled-down PIL image.

  Args:
    slide_number: The slide number.

  Returns:
    Tuple consisting of scaled-down PIL image, original width, original height, new width, and new height.
  """
  sl = openslide.open_slide(str(slide_filepath))

  large_w, large_h = sl.dimensions
  new_w = math.floor(large_w / slide.SCALE_FACTOR)
  new_h = math.floor(large_h / slide.SCALE_FACTOR)
  level = sl.get_best_level_for_downsample(slide.SCALE_FACTOR)
  whole_slide_image = sl.read_region((0, 0), level, sl.level_dimensions[level])
  whole_slide_image = whole_slide_image.convert("RGB")
  img = whole_slide_image.resize((new_w, new_h), PIL.Image.BILINEAR)
  return img, large_w, large_h, new_w, new_h

slide.slide_to_scaled_pil_image = slide_to_scaled_pil_image


def training_slide_to_image(slide_filepath):
  """
  Convert a WSI training slide to a saved scaled-down image in a format such as jpg or png.

  Args:
    slide_number: The slide number.
  """
  img, large_w, large_h, new_w, new_h = slide_to_scaled_pil_image(slide_filepath)
  img_path = f'{rois_path}/{slide_filepath.stem}-scale_factor_{slide.SCALE_FACTOR}.png'
  print("Saving image to: " + img_path)
  img.save(img_path)

slide.training_slide_to_image = training_slide_to_image

##############################################################################################

def summary_and_tiles(slide_num, display=True, save_summary=False, save_data=True, save_top_tiles=True):
  """
  Generate tile summary and top tiles for slide.

  Args:
    slide_num: The slide number.
    display: If True, display tile summary to screen.
    save_summary: If True, save tile summary images.
    save_data: If True, save tile data to csv file.
    save_top_tiles: If True, save top tiles to files.

  """
  img_path = slide.get_filter_image_result(slide_num)
  np_img = slide.open_image_np(img_path)

  tile_sum = tiles.score_tiles(slide_num, np_img)
  if save_data:
    tiles.save_tile_data(tile_sum)
  #generate_tile_summaries(tile_sum, np_img, display=display, save_summary=save_summary)
  #generate_top_tile_summaries(tile_sum, np_img, display=display, save_summary=save_summary)
  if save_top_tiles:
    for tile in tile_sum.top_tiles():
      tile.save_tile()
  return tile_sum

tiles.summary_and_tiles = summary_and_tiles

# Convert WSIs

In [5]:
#def convert_wsi_to_png(path:pathlib.Path, index:int):
#    #try:
#        slide.training_slide_to_image(path)
#        print(f'Saved {path.stem}.png')
#    #except:
#        #print(path)
#        
#fastai.core.parallel(convert_wsi_to_png, wsi_path.ls(), max_workers=20)

In [ ]:
for p in tqdm(wsi_path.ls()):
    for b in rois_path.ls():
        if p.stem == b.stem:
            break
    else:
        slide.training_slide_to_image(p)

# Filter images

In [29]:
##
# for 'normal' img formats like .png
# fastai's parallel function expects a function that takes a value and an index, for that reason 
# filter_roi accepts the 'index' parameter, it can be ignored
##

def filter_roi(img_path:pathlib.Path, index:int = 0):
    if img_path.suffix == '.png':
        try:
            img_pil = slide.open_image(img_path)
            img_np = util.pil_to_np_rgb(img_pil)
            grayscale_np = filter.filter_rgb_to_grayscale(img_np)
            complement_np = filter.filter_complement(grayscale_np)
            otsu_np = filter.filter_otsu_threshold(complement_np).astype(np.bool)
            filtered_img_np = util.mask_rgb(img_np, otsu_np)
            #filtered_path = rois_filtered_path/f'{img_path.stem}-filtered{img_path.suffix}'
            filtered_path = rois_filtered_path/f'{img_path.stem}{img_path.suffix}'
            try:
                filtered_img_pil = util.np_to_pil(filtered_img_np)
                filtered_img_pil.save(filtered_path)
            except ValueError as e:
                print(f'PIL failed, using cv2 instead. {img_path}')
                #cv2 expects the array to have bgr as channel order
                bgr = filtered_img_np[...,[2,1,0]]
                cv2.imwrite(str(filtered_path), bgr)
        except:
            print(f'The error occured during the filtering process or PIL and cv2 failed to save it. {img_path}')
            raise
            

In [31]:
rois_path.ls()[4919]

PosixPath('/home/Deep_Learner/private/network/datasets/Hypophysenadenome/gonadotrop_ROIs/1153-13-III-HE-ROI_11-LH+FSH.png')

In [33]:
filter_roi(rois_path.ls()[4919])

RGB                  | Time: 0:00:14.414048  Type: uint8   Shape: (25513, 30081, 3)
Gray                 | Time: 0:00:19.903783  Type: uint8   Shape: (25513, 30081)
Complement           | Time: 0:00:00.182002  Type: uint8   Shape: (25513, 30081)
Otsu Threshold       | Time: 0:00:06.103240  Type: uint8   Shape: (25513, 30081)
Mask RGB             | Time: 0:00:02.036067  Type: uint8   Shape: (25513, 30081, 3)
PIL failed, using cv2 instead. /home/Deep_Learner/private/network/datasets/Hypophysenadenome/gonadotrop_ROIs/1153-13-III-HE-ROI_11-LH+FSH.png


In [34]:
rois_filtered_path.ls()[4919]

PosixPath('/home/Deep_Learner/private/network/datasets/Hypophysenadenome/rois_gonadotrop_filtered/1153-13-III-HE-ROI_11-LH+FSH.png')

In [5]:
###
# use this line instead of the following for loop to do the filtering in parallel with mutiple threads
###
#parallel(filter_roi, rois_path.ls(), max_workers=25)

#failed = []
for p in tqdm(rois_path.ls()):
    #try:
        filter_roi(p)
    #except:
        #failed.append(p)
    
#print(failed)

RGB                  | Time: 0:00:07.352323  Type: uint8   Shape: (16128, 14336, 3)
Gray                 | Time: 0:00:11.113000  Type: uint8   Shape: (16128, 14336)
Complement           | Time: 0:00:00.070322  Type: uint8   Shape: (16128, 14336)
Otsu Threshold       | Time: 0:00:02.144515  Type: uint8   Shape: (16128, 14336)
Mask RGB             | Time: 0:00:00.794553  Type: uint8   Shape: (16128, 14336, 3)
RGB                  | Time: 0:00:12.326676  Type: uint8   Shape: (21504, 17920, 3)
Gray                 | Time: 0:00:18.222186  Type: uint8   Shape: (21504, 17920)
Complement           | Time: 0:00:00.111731  Type: uint8   Shape: (21504, 17920)
Otsu Threshold       | Time: 0:00:03.484084  Type: uint8   Shape: (21504, 17920)
Mask RGB             | Time: 0:00:01.300631  Type: uint8   Shape: (21504, 17920, 3)
RGB                  | Time: 0:01:26.960319  Type: uint8   Shape: (45696, 59136, 3)
Gray                 | Time: 0:02:08.530854  Type: uint8   Shape: (45696, 59136)
Complement   

PIL failed, using cv2 instead. /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/imgs_non_relapse/711-12-III-HE-scale_factor_2.png
RGB                  | Time: 0:00:14.969793  Type: uint8   Shape: (18816, 17920, 3)
Gray                 | Time: 0:00:19.668405  Type: uint8   Shape: (18816, 17920)
Complement           | Time: 0:00:00.137808  Type: uint8   Shape: (18816, 17920)
Otsu Threshold       | Time: 0:00:03.390516  Type: uint8   Shape: (18816, 17920)
Mask RGB             | Time: 0:00:01.335997  Type: uint8   Shape: (18816, 17920, 3)
RGB                  | Time: 0:00:17.707281  Type: uint8   Shape: (18816, 25088, 3)
Gray                 | Time: 0:00:27.483334  Type: uint8   Shape: (18816, 25088)
Complement           | Time: 0:00:00.180145  Type: uint8   Shape: (18816, 25088)
Otsu Threshold       | Time: 0:00:04.677538  Type: uint8   Shape: (18816, 25088)
Mask RGB             | Time: 0:00:01.870887  Type: uint8   Shape: (18816, 25088, 3)
RGB                  | Tim

RGB                  | Time: 0:00:08.874318  Type: uint8   Shape: (13440, 16128, 3)
Gray                 | Time: 0:00:12.714951  Type: uint8   Shape: (13440, 16128)
Complement           | Time: 0:00:00.085190  Type: uint8   Shape: (13440, 16128)
Otsu Threshold       | Time: 0:00:02.205660  Type: uint8   Shape: (13440, 16128)
Mask RGB             | Time: 0:00:00.898730  Type: uint8   Shape: (13440, 16128, 3)
RGB                  | Time: 0:00:19.893420  Type: uint8   Shape: (21504, 23296, 3)
Gray                 | Time: 0:00:29.104551  Type: uint8   Shape: (21504, 23296)
Complement           | Time: 0:00:00.185045  Type: uint8   Shape: (21504, 23296)
Otsu Threshold       | Time: 0:00:05.045240  Type: uint8   Shape: (21504, 23296)
Mask RGB             | Time: 0:00:02.055000  Type: uint8   Shape: (21504, 23296, 3)
RGB                  | Time: 0:00:35.988558  Type: uint8   Shape: (26880, 34048, 3)
Gray                 | Time: 0:00:53.081588  Type: uint8   Shape: (26880, 34048)
Complement   

## Fix for PIL Value Error
PIL raises an ValueEerror, when using Image.fromarray() with very big numpy arrays.
In this case use cv2. Beware that you have to switch rgb to bgr in numpy array before saving.

In [ ]:
pa = Path('/home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/imgs_relapse/495-09-III-HE-scale_factor_2.png')

In [ ]:
img_pil = slide.open_image(pa)
img_np = util.pil_to_np_rgb(img_pil)
grayscale_np = filter.filter_rgb_to_grayscale(img_np)
complement_np = filter.filter_complement(grayscale_np)
otsu_np = filter.filter_otsu_threshold(complement_np).astype(np.bool)
filtered_img_np = util.mask_rgb(img_np, otsu_np)

In [ ]:
plt.imshow(filtered_img_np)

In [ ]:
filtered_path = rois_filtered_path/f'{pa.stem}{pa.suffix}'

In [ ]:
try:
    filtered_img_pil = util.np_to_pil(filtered_img_np)
    filtered_img_pil.save(filtered_path)
except ValueError as e:
    bgr = filtered_img_np[...,[2,1,0]]
    cv2.imwrite(str(filtered_path), bgr)

In [ ]:
ü = filtered_img_np[10000:12000,3500:5000,:]

In [ ]:
plt.imshow(ü)

In [ ]:
path_pil = rois_filtered_path/f'{pa.stem}-pil-{pa.suffix}'
filtered_img_pil = util.np_to_pil(ü)

In [ ]:
path_cv = rois_filtered_path/f'{pa.stem}-cv2-{pa.suffix}'
bgr = ü[...,[2,1,0]]
cv2.imwrite(str(path_cv), bgr)

In [ ]:
open_image(path_cv)

In [ ]:
open_image(path_pil)

# Create tiles

## multi process

In [ ]:
tiles.multiprocess_filtered_images_to_tiles(display=False, 
                                            save_summary=False, 
                                            save_data=False, 
                                            save_top_tiles=True,
                                            html=False, 
                                            image_num_list=list(range(0, len(rois_filtered_path.ls()))))

Generating tile summaries (multiprocess)

Number of processes: 32
Number of training images: 39
Task #1: Process slides [0]
Task #2: Process slides [1]
Task #3: Process slides [2]
Task #4: Process slides [3]
Task #5: Process slides [4, 5]
Task #6: Process slides [6]
Task #7: Process slides [7]
Task #8: Process slides [8]
Task #9: Process slides [9]
Task #10: Process slides [10, 11]
Task #11: Process slides [12]
Task #12: Process slides [13]
Task #13: Process slides [14]
Task #14: Process slides [15, 16]
Task #15: Process slides [17]
Task #16: Process slides [18]
Task #17: Process slides [19]
Task #18: Process slides [20]
Task #19: Process slides [21, 22]
Task #20: Process slides [23]
Task #21: Process slides [24]
Task #22: Process slides [25]
Task #23: Process slides [26, 27]
Task #24: Process slides [28]
Task #25: Process slides [29]
Task #26: Process slides [30]
Task #27: Process slides [31]
Task #28: Process slides [32, 33]
Task #29: Process slides [34]
Task #30: Process slides [35]

/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:265: RuntimeWarning: divide by zero encountered in true_divide
  out_s = delta / out_v
/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:271: RuntimeWarning: divide by zero encountered in true_divide
  out[idx, 0] = (arr[idx, 1] - arr[idx, 2]) / delta[idx]
/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:275: RuntimeWarning: divide by zero encountered in true_divide
  out[idx, 0] = 2. + (arr[idx, 2] - arr[idx, 0]) / delta[idx]
/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:279: RuntimeWarning: divide by zero encountered in true_divide
  out[idx, 0] = 4. + (arr[idx, 0] - arr[idx, 1]) / delta[idx]


RGB                  | Time: 0:00:02.430851  Type: uint8   Shape: (13440, 5376, 3)
RGB                  | Time: 0:00:04.947042  Type: uint8   Shape: (10752, 14336, 3)


/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:265: RuntimeWarning: divide by zero encountered in true_divide
  out_s = delta / out_v
/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:271: RuntimeWarning: divide by zero encountered in true_divide
  out[idx, 0] = (arr[idx, 1] - arr[idx, 2]) / delta[idx]
/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:275: RuntimeWarning: divide by zero encountered in true_divide
  out[idx, 0] = 2. + (arr[idx, 2] - arr[idx, 0]) / delta[idx]
/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:279: RuntimeWarning: divide by zero encountered in true_divide
  out[idx, 0] = 4. + (arr[idx, 0] - arr[idx, 1]) / delta[idx]


RGB                  | Time: 0:00:06.468344  Type: uint8   Shape: (16128, 14336, 3)
RGB                  | Time: 0:00:08.041677  Type: uint8   Shape: (13440, 16128, 3)
RGB                  | Time: 0:00:03.985330  Type: uint8   Shape: (10752, 14336, 3)
RGB                  | Time: 0:00:09.990776  Type: uint8   Shape: (13440, 21504, 3)


...

RGB                  | Time: 0:00:44.113477  Type: uint8   Shape: (32256, 41216, 3)
Save Tile            | Time: 0:00:00.066915  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/670-12-III-HE-scale_factor_2-tile-r41-c64-x64512-y40960-w1024-h1024.png
RGB                  | Time: 0:14:05.220565  Type: uint8   Shape: (48384, 62720, 3)
Save Tile            | Time: 0:00:00.068960  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/206-12-III-HE-scale_factor_2-tile-r72-c55-x55296-y72704-w1024-h1024.png
RGB                  | Time: 0:14:07.968998  Type: uint8   Shape: (48384, 57344, 3)
Save Tile            | Time: 0:00:00.067978  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/1340-12-III-HE-scale_factor_2-tile-r30-c72-x72704-y29696-w1024-h1024.png
RGB                  | Time: 0:00:51.818775  Type: uint8   Shape: (32256, 48384, 3)
Save Tile            | Time

RGB                  | Time: 0:01:16.988046  Type: uint8   Shape: (48384, 48384, 3)
Save Tile            | Time: 0:00:00.137598  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/131-12-III-HE-scale_factor_2-tile-r72-c60-x60416-y72704-w1024-h1024.png
RGB                  | Time: 0:01:08.892074  Type: uint8   Shape: (37632, 55552, 3)
Save Tile            | Time: 0:00:00.051405  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/671-12-III-HE-scale_factor_2-tile-r40-c102-x103424-y39936-w1024-h1024.png
RGB                  | Time: 0:02:18.811310  Type: uint8   Shape: (40320, 53760, 3)
Save Tile            | Time: 0:00:00.074437  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/630-12-IV-HE-scale_factor_2-tile-r22-c27-x26624-y21504-w1024-h1024.png
RGB                  | Time: 0:01:41.798456  Type: uint8   Shape: (32256, 41216, 3)
Save Tile            | Time

RGB                  | Time: 0:00:43.747950  Type: uint8   Shape: (32256, 41216, 3)
Save Tile            | Time: 0:00:00.100155  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/670-12-III-HE-scale_factor_2-tile-r19-c43-x43008-y18432-w1024-h1024.png
RGB                  | Time: 0:06:04.829441  Type: uint8   Shape: (40320, 59136, 3)
Save Tile            | Time: 0:00:00.070095  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/1006-12-IV-HE-scale_factor_2-tile-r71-c67-x67584-y71680-w1024-h1024.png
RGB                  | Time: 0:00:44.015675  Type: uint8   Shape: (32256, 41216, 3)
Save Tile            | Time: 0:00:00.082648  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/670-12-III-HE-scale_factor_2-tile-r17-c14-x13312-y16384-w1024-h1024.png
RGB                  | Time: 0:04:18.779653  Type: uint8   Shape: (43008, 48384, 3)
Save Tile            | Time:

RGB                  | Time: 0:01:09.299233  Type: uint8   Shape: (37632, 55552, 3)
Save Tile            | Time: 0:00:00.060918  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/671-12-III-HE-scale_factor_2-tile-r40-c46-x46080-y39936-w1024-h1024.png
RGB                  | Time: 0:01:08.884495  Type: uint8   Shape: (43008, 48384, 3)
Save Tile            | Time: 0:00:00.066469  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/261-12-IV-HE-scale_factor_2-tile-r49-c9-x8192-y49152-w1024-h1024.png
RGB                  | Time: 0:00:43.985679  Type: uint8   Shape: (32256, 41216, 3)
Save Tile            | Time: 0:00:00.073953  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/670-12-III-HE-scale_factor_2-tile-r39-c74-x74752-y38912-w1024-h1024.png
RGB                  | Time: 0:01:11.947250  Type: uint8   Shape: (40320, 53760, 3)
Save Tile            | Time: 0:

RGB                  | Time: 0:01:11.552748  Type: uint8   Shape: (40320, 53760, 3)
Save Tile            | Time: 0:00:00.058004  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/630-12-IV-HE-scale_factor_2-tile-r52-c39-x38912-y52224-w1024-h1024.png
RGB                  | Time: 0:01:08.510638  Type: uint8   Shape: (43008, 48384, 3)
Save Tile            | Time: 0:00:00.059985  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/261-12-IV-HE-scale_factor_2-tile-r59-c37-x36864-y59392-w1024-h1024.png
RGB                  | Time: 0:04:39.013817  Type: uint8   Shape: (45696, 46592, 3)
Save Tile            | Time: 0:00:00.048667  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/510-13-III-HE-scale_factor_2-tile-r45-c52-x52224-y45056-w1024-h1024.png
RGB                  | Time: 0:00:52.143018  Type: uint8   Shape: (32256, 48384, 3)
Save Tile            | Time: 0

In [10]:
print(len(tiles_path.ls()))

l = []
for p in tqdm(tiles_path.ls()):
    l.append(get_wsi_name_from_path(p))

print(len(set(l)))
print(set(l))

17009



37
{'1567-12-III-HE', '865-13-III-HE', '678-12-III-HE', '1739-12-IV-HE', '630-12-IV-HE', '1668-13-III-HE', '788-13-III-HE', '1787-12-V-HE', '131-12-III-HE', '1182-12-III-HE', '692-12-III-HE', '671-12-III-HE', '206-12-III-HE', '1579-12-III-HE', '261-12-IV-HE', '772-12-III-HE', '1882-12-III-HE', '1285-12-II-HE', '631-12-IV-HE', '1722-12-Z-HE', '1006-12-IV-HE', '1314-12-Z-HE', '670-12-III-HE', '84-13-III-HE', '1572-13-III-HE', '464-13-IV-HE', '1583-13-III-HE', '400-13-III-HE', '510-13-III-HE', '31-12-III-HE', '1048-12-III-HE', '1787-12-III-HE', '464-13-III-HE', '1739-12-III-HE', '1630-13-III-HE', '1340-12-III-HE', '848-13-III-HE'}


In [ ]:
show_multiple_images_big(tiles_path)

In [ ]:
#!rm -r {rois_filtered_path/'*'}
#!rm -r {tiles_path/'*'}

## single process

In [ ]:
#!rm -r {tiles_path/'*'}

In [14]:
ids = []
for p in tiles_path.ls():
    ids.append(get_wsi_name_from_path(p))

In [15]:
for p in rois_filtered_path.ls():
    if not get_wsi_name_from_path(p) in ids:
        print(get_wsi_name_from_path(p))

841-12-III-HE
711-12-III-HE


In [16]:
failed = []
for n, p in tqdm(enumerate(rois_filtered_path.ls()), total=len(rois_filtered_path.ls())):
    if p.suffix == '.png' and (get_wsi_name_from_path(p) not in ids):
        try:
            print(p)
            tiles.summary_and_tiles(n, display=False, save_summary=False, save_data=False, save_top_tiles=True)
        except:
            failed.append(p)
            
print(failed)

/home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/imgs_filtered_non_relapse/841-12-III-HE-scale_factor_2.png
RGB                  | Time: 0:00:25.226582  Type: uint8   Shape: (32256, 35840, 3)
RGB                  | Time: 0:01:23.637425  Type: uint8   Shape: (32256, 35840, 3)


/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:265: RuntimeWarning: divide by zero encountered in true_divide
  out_s = delta / out_v
/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:271: RuntimeWarning: divide by zero encountered in true_divide
  out[idx, 0] = (arr[idx, 1] - arr[idx, 2]) / delta[idx]
/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:275: RuntimeWarning: divide by zero encountered in true_divide
  out[idx, 0] = 2. + (arr[idx, 2] - arr[idx, 0]) / delta[idx]
/opt/conda/lib/python3.7/site-packages/skimage/color/colorconv.py:279: RuntimeWarning: divide by zero encountered in true_divide
  out[idx, 0] = 4. + (arr[idx, 0] - arr[idx, 1]) / delta[idx]


Number of top tiles/all tiles: 1597/4410
RGB                  | Time: 0:02:04.485180  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time: 0:00:00.072902  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/841-12-III-HE-scale_factor_2-tile-r22-c32-x31744-y21504-w1024-h1024.png
RGB                  | Time: 0:05:11.023283  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time: 0:00:00.074919  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/841-12-III-HE-scale_factor_2-tile-r30-c22-x21504-y29696-w1024-h1024.png
RGB                  | Time: 0:00:39.791918  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time: 0:00:00.077029  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/841-12-III-HE-scale_factor_2-tile-r40-c57-x57344-y39936-w1024-h1024.png
RGB                  | Time: 0:00:39.424210  Type: uint8   Shape: (3225

RGB                  | Time: 0:00:39.525079  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time: 0:00:00.108171  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/841-12-III-HE-scale_factor_2-tile-r35-c42-x41984-y34816-w1024-h1024.png
RGB                  | Time: 0:03:52.048383  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time: 0:00:00.065786  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/841-12-III-HE-scale_factor_2-tile-r17-c56-x56320-y16384-w1024-h1024.png
RGB                  | Time: 0:00:38.986897  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time: 0:00:00.072992  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/841-12-III-HE-scale_factor_2-tile-r51-c53-x53248-y51200-w1024-h1024.png
RGB                  | Time: 0:00:39.205521  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time:

RGB                  | Time: 0:00:39.279544  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time: 0:00:00.079276  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/841-12-III-HE-scale_factor_2-tile-r40-c55-x55296-y39936-w1024-h1024.png
RGB                  | Time: 0:02:04.833454  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time: 0:00:00.065795  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/841-12-III-HE-scale_factor_2-tile-r26-c24-x23552-y25600-w1024-h1024.png
RGB                  | Time: 0:01:45.556867  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time: 0:00:00.069366  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/841-12-III-HE-scale_factor_2-tile-r28-c23-x22528-y27648-w1024-h1024.png
RGB                  | Time: 0:00:39.054260  Type: uint8   Shape: (32256, 35840, 3)
Save Tile            | Time:

...

RGB                  | Time: 0:00:50.538380  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.057037  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r38-c21-x20480-y37888-w1024-h1024.png
RGB                  | Time: 0:00:50.622168  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.054159  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r17-c63-x63488-y16384-w1024-h1024.png
RGB                  | Time: 0:00:50.349521  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.083866  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r13-c36-x35840-y12288-w1024-h1024.png
RGB                  | Time: 0:00:50.873685  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time:

RGB                  | Time: 0:00:50.535773  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.053743  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r16-c63-x63488-y15360-w1024-h1024.png
RGB                  | Time: 0:00:50.306650  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.050464  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r46-c23-x22528-y46080-w1024-h1024.png
RGB                  | Time: 0:00:50.459836  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.054221  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r21-c23-x22528-y20480-w1024-h1024.png
RGB                  | Time: 0:00:50.619035  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time:

RGB                  | Time: 0:00:50.549941  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.055254  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r10-c62-x62464-y9216-w1024-h1024.png
RGB                  | Time: 0:00:50.344249  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.048285  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r50-c66-x66560-y50176-w1024-h1024.png
RGB                  | Time: 0:00:50.412278  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.052274  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r22-c21-x20480-y21504-w1024-h1024.png
RGB                  | Time: 0:00:50.463050  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 

RGB                  | Time: 0:00:50.693877  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.080300  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r9-c37-x36864-y8192-w1024-h1024.png
RGB                  | Time: 0:00:50.541188  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.059133  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r44-c36-x35840-y44032-w1024-h1024.png
RGB                  | Time: 0:00:50.716502  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.064251  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r16-c68-x68608-y15360-w1024-h1024.png
RGB                  | Time: 0:00:50.491257  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0

RGB                  | Time: 0:00:50.639116  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.054188  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r30-c31-x30720-y29696-w1024-h1024.png
RGB                  | Time: 0:00:50.974488  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.053149  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r31-c80-x80896-y30720-w1024-h1024.png
RGB                  | Time: 0:00:50.388653  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0:00:00.090676  Name: /home/Deep_Learner/private/network/datasets/Hypophysenadenome-Rezidive/tiles_non_relapse/711-12-III-HE-scale_factor_2-tile-r8-c44-x44032-y7168-w1024-h1024.png
RGB                  | Time: 0:00:50.584625  Type: uint8   Shape: (32256, 46592, 3)
Save Tile            | Time: 0

In [14]:
for n, p in tqdm(enumerate(rois_filtered_path.ls()), total=len(rois_filtered_path.ls())):
    if p.name == '1314-12-Z-HE-scale_factor_2.png':
        print(n)

2



In [ ]:
tiles.summary_and_tiles(2, display=False, save_summary=False, save_data=False, save_top_tiles=True)

## Extract tiles from cases, where no tiles were extracted in the first run

In [92]:
def get_roi_name_from_path(path):
        split = path.stem.split('-')
        if split[2] == 'HE':
                return f'{split[0]}-{split[1]}-{split[2]}-{split[3]}-{split[4]}'
        else:
            return f'{split[0]}-{split[1]}-{split[2]}-{split[3]}-{split[4]}-{split[5]}'

In [94]:
rois_path

PosixPath('/home/Deep_Learner/private/network/datasets/Hypophysenadenome/gonadotrop_ROIs')

In [95]:
tiles_path

PosixPath('/home/Deep_Learner/private/network/datasets/Hypophysenadenome/tiles_gonadotrop_extra')

In [96]:
rois_names = [get_roi_name_from_path(p) for p in rois_path.ls()]
rois_filtered_names = [get_roi_name_from_path(p) for p in rois_filtered_path.ls()]
tiles_names = [get_roi_name_from_path(p) for p in TILES_GONADOTROP.ls()]

print(len(set(rois_names)))
print(len(rois_names))
print(len(set(rois_filtered_names)))
print(len(set(tiles_names)))

7796
7796
7796
4958


In [104]:
indices_rois_no_tiles_extracted_yet = []  
for n, p in tqdm(enumerate(rois_path.ls()), total=len(rois_path.ls())):
    roi_name = get_roi_name_from_path(p)
    if roi_name in tiles_names:
        continue
    else:
        indices_rois_no_tiles_extracted_yet.append(n)

In [105]:
###Should be true
len(set(rois_names)) - len(set(tiles_names)) == len(indices_rois_no_tiles_extracted_yet)

True

In [ ]:
tiles.multiprocess_filtered_images_to_tiles(display=False, 
                                            save_summary=False, 
                                            save_data=False, 
                                            save_top_tiles=True,
                                            html=False, 
                                            image_num_list=indices_rois_no_tiles_extracted_yet)

# exp

In [ ]:
import PIL
p = '/home/Deep_Learner/work/network/datasets/Hypophysenadenome/rois_corticotrop/1000-13-III-HE-ROI_1-ACTH.png'

img_pil = slide.open_image(p)
img_np = util.pil_to_np_rgb(img_pil)
grayscale_np = filter.filter_rgb_to_grayscale(img_np)
complement_np = filter.filter_complement(grayscale_np)
otsu_np = filter.filter_otsu_threshold(complement_np).astype(np.bool)
filtered_img_np = util.mask_rgb(img_np, otsu_np)

plt.imshow(filtered_img_np)

tiles = []
sz = 512
for i in range(int(filtered_img_np.shape[0]/sz)):
    for j in range(int(filtered_img_np.shape[1]/sz)):
         tiles.append(filtered_img_np[i*sz:(i+1)*sz,j*sz:(j+1)*sz])
        

for t in tiles:
    print(t.shape)
    nz = np.count_nonzero(t)// 3
    print(f'tissue percentage:{(nz/(t.shape[0]*t.shape[1]))*100}')
    plt.imshow(t)
    plt.show()